# Charachteristic Event Meteorology
### Author: Daniel Hogan
### Creation Date: July 29, 2024

This notebook will go through some surface measurements during some characteristic and extreme blowing snow sublimation events during the SOS and SAIL/SPLASH campaigns. 
Four of these events were during the 2023 winter, while 1 was during the 2022 winter

### Imports

In [1]:
# general
import os
import glob
import datetime as dt
import json
# data 
import xarray as xr 
from sublimpy import utils, variables, tidy, turbulence
import numpy as np
import pandas as pd
from act import discovery, plotting
# plotting
import matplotlib.pyplot as plt
import plotly.express as px 
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import cufflinks as cf
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
# helper tools
from scripts.get_sail_data import get_sail_data
from scripts.helper_funcs import create_windrose_df, simple_sounding, mean_sounding
import scripts.helper_funcs as hf
from metpy import calc, units
# make plotly work 
init_notebook_mode(connected=True)
cf.go_offline()
# stats
import scipy.stats as stats
import seaborn as sns


nctoolkit is using Climate Data Operators version 2.3.0


### Data

In [47]:
# laser disdrometer data
w23_ld_gts_ds = xr.open_dataset('../../01_data/processed_data/sail_processed/precipitation_rate_gts_w23.nc')
w23_prcp_rate_gts_ds = w23_ld_gts_ds.sel(time=slice('2022-12-01', '2023-03-31'))[['corrected_prcp_rate_m2', 'qc_precip_rate']]
# SPLASH laser disdrometer data
w23_SPLASH_kp_ld = xr.open_dataset('../../01_data/processed_data/splash/corrected_ldis_precipitation_rate_kps_w23.nc').sel(time=slice('2022-12-01','2023-03-31'))

# winter 2022 laser disdrometer data
w22_ld_gts_ds = xr.open_dataset('../../01_data/processed_data/sail_processed/precipitation_rate_gts_w22.nc')
w22_prcp_rate_gts_ds = w22_ld_gts_ds.sel(time=slice('2021-12-01', '2022-03-31'))[['corrected_prcp_rate_m2', 'qc_precip_rate']]
w22_SPLASH_kp_ld = xr.open_dataset('../../01_data/processed_data/splash/corrected_ldis_precipitation_rate_kps_w22.nc').sel(time=slice('2021-12-01','2022-03-31'))

# blowing snow data
sos_ds_5min = xr.open_dataset('../../01_data/processed_data/sos_ds_5min_storage.nc')
sos_ds_5min = sos_ds_5min.sel(time=slice('2022-12-01', '2023-03-31')).to_dataframe().resample('5min').mean().to_xarray()

# wind data
w22_sail_gts_met = xr.open_dataset('/storage/dlhogan/synoptic_sublimation/sail_data/winter_21_22/met_20211001_20220930.nc')
w22_sail_gts_met = w22_sail_gts_met.sel(time=slice('2021-12-01', '2022-03-31')).drop_dims('bound').to_dataframe().resample('5min').mean().to_xarray()
w22_sail_kp_ecor_1H = xr.open_dataset('../../01_data/processed_data/sail_processed/sail_ds_1H_met_kp_2022.nc').sel(time=slice('2021-12-01', '2022-03-31'))
w22_sail_gts_met_1H = xr.open_dataset('../../01_data/processed_data/sail_processed/sail_ds_1H_met_2022.nc')

# SPLASH wind and sublimation data
w22_splash_kp_asfs = xr.open_dataset('../../01_data/processed_data/splash/w22_splash_kp_qc_1H.nc').sel(time=slice('2021-12-01','2022-03-31'))
ap_splash_22 = xr.open_dataset('../../01_data/processed_data/splash/w22_splash_ap_qc_1H.nc').sel(time=slice('2021-12-01','2022-03-31'))

# SPLASH ceilometer data
w23_splash_kp_ceil = xr.open_dataset('/storage/dlhogan/synoptic_sublimation/splash_data/ceilometer/splash_kp_ceilometer.nc').sel(time=slice('2022-10-01','2023-03-31'))

### Make adjustments to data for plotting

First, let's add sublimation (hourly-rate) to the SOS-data

In [67]:
# filter to the desired variables
sos_5min_h2o_flux_ds = sos_ds_5min[[variable for variable in hf.TURBULENCE_VARIABLES if 'w_h2o' in variable]+[variable for variable in hf.COUNT_VARIABLES]+hf.SNOW_FLUX+hf.WIND_VARIABLES+hf.TEMPERATURE_VARIABLES+hf.PRESSURE_VARIABLES]

rho_w = 1000
g2kg = 1/1000
s_in_hour = 3600
sublimation_1H = (sos_5min_h2o_flux_ds[[variable for variable in hf.TURBULENCE_VARIABLES if 'w_h2o' in variable]] * 1/rho_w * 1000 * g2kg * s_in_hour).to_dataframe()
# get the mean at the 3 meter height
sublimation_1H = sublimation_1H[[var for var in sublimation_1H if 'w_h2o__5m' in var]].mean(axis=1).to_frame()
sublimation_1H.columns = ['sublimation_hourly_rate']
sos_5min_h2o_flux_ds['sublimation_hourly_rate'] = sublimation_1H.to_xarray()['sublimation_hourly_rate']

# add the precipitation rate to the dataset
sos_5min_h2o_flux_ds['precip_rate'] = w23_SPLASH_kp_ld['corrected_prcp_rate_m2']


In [49]:
# only if needed
# adjust wdir
def adjust_wdir(ds):
    new_df = ds.to_dataframe()
    new_ds = hf.adjust_wdir(new_df).to_xarray()
    ## Copy attributes from the original dataset
    new_ds.attrs = ds.attrs
    for var in new_ds:
        new_ds[var].attrs = ds[var].attrs
    return new_ds
# sos_1H_h2o_flux_ds = adjust_wdir(sos_1H_h2o_flux_ds)

Next, let's add a sublimation variable to the SAIL data that is numerically complete

In [50]:
x = ap_splash_22['Hl'].dropna('time')
y = w22_splash_kp_asfs['Hl'].sel(time=x.time).dropna('time')
x = x.sel(time=y.time)

# linear regression
slope, intercept, r, p, stderr = stats.linregress(x, y)

# use the regression to fill nan in kp_splash_22['Hl']
x1 = ap_splash_22['Hl']
# filled these values, but they are uncertain!!!!
w22_splash_kp_asfs['Hl'] = w22_splash_kp_asfs['Hl'].where(~w22_splash_kp_asfs['Hl'].isnull(), x1*slope + intercept)

# add kp_splash_22['Hl'] and convert from W/m^2 to mm/hr -> filled with SPLASH values
w22_sail_kp_ecor_1H['sublimation'] = (w22_splash_kp_asfs['Hl'] * 3600 / (2834.1e3))
w22_sail_kp_ecor_1H['wind_spd'] = w22_splash_kp_asfs['wspd_vec_mean']
w22_sail_kp_ecor_1H['wind_dir'] = w22_splash_kp_asfs['wdir_vec_mean']

Replace pressure and temperature variables with w22_sail_gts_met

In [51]:
w22_sail_kp_ecor_1H['atm_pres'] = w22_sail_gts_met['atmos_pressure']
w22_sail_kp_ecor_1H['mean_t'] = w22_sail_gts_met['temp_mean']


### Make a function to plot the desired variables.

In [75]:

def plot_event_met(ds, dates, vars, var_type_dict):
    fig = make_subplots(rows=len(vars), cols=1, shared_xaxes=True, vertical_spacing=0.02)
    for i, var in enumerate(vars):
        tmp_ds = ds.sel(time=slice(dates[0],dates[1]))[var].dropna('time')
        if 'dir' not in var:
            fig.add_trace(go.Scatter(x=tmp_ds.time, y=tmp_ds, mode='lines', name=var), row=i+1, col=1)
        else:
            fig.add_trace(go.Scatter(x=tmp_ds.time, y=tmp_ds, mode='markers', name=var, line=dict(color='red')), row=i+1, col=1)
        fig.update_yaxes(title_text=f'{var_type_dict[var]["name"]}<br>({var_type_dict[var]["units"]})', row=i+1, col=1)
    fig.update_xaxes(title_text='Time', row=len(vars), col=1)
    fig.update_layout(height=800, width=1000, title_text=f'{dates[0]} to {dates[1]}')
    # add a hovermode 
    fig.update_layout(hovermode='x')
    fig.show()
    return

### December 24-January 1, 2021 - Santa Slammer Event
Tons of precipitation fell, we'll take a look at what winds did, how pressure changed, what sublimation was measured (hourly rates), and what humidity did using SAIL and SPLASH data.

In [76]:
dates = ['2021-12-24', '2022-01-01']
vars = ['atm_pres', 'mean_t', 'wind_spd', 'wind_dir', 'sublimation', 'precip_rate']
var_type_dict = {'sublimation':
                 dict(name='sublimation',
                      units='mm/hr',),
                    'atm_pres':
                    dict(name='atm_pres',
                        units='hPa',),
                    'mean_t':
                    dict(name='mean_t',
                        units='C',),
                    'wind_spd':
                    dict(name='wind_speed',
                        units='m/s',),
                    'wind_dir':
                    dict(name='wind_dir',
                        units='degrees',),
                    'precip_rate':
                    dict(name='precip_rate',
                        units='mm/hr',)}
                    
plot_event_met(w22_sail_kp_ecor_1H, dates, vars, var_type_dict)

### December 21-22, 2022 - Biggest wind event of winter 2023
This event was characterized by a consistent, relatively stationary NW-SE oriented front that kept howling, strong winds at the site. Precipitation occurred, as well.

In [77]:
dates = ['2022-12-21', '2022-12-24']
vars = ['P_10m_c', 'T_3m_c', 'spd_10m_c', 'dir_10m_c', 'sublimation_hourly_rate', 'precip_rate', 'SF_avg_1m_ue']
var_type_dict = {'sublimation_hourly_rate':
                    dict(name='sublimation',
                        units='mm/hr',),
                        'P_10m_c':
                        dict(name='atm_pres',
                            units='hPa',),
                        'T_3m_c':
                        dict(name='T_3m_c',
                            units='C',),
                        'spd_10m_c':
                        dict(name='spd_10m_c',
                            units='m/s',),
                        'dir_10m_c':
                        dict(name='dir_10m_c',
                            units='degrees',),
                        'precip_rate':
                        dict(name='precip_rate',
                            units='mm/hr',),
                        'SF_avg_1m_ue':
                        dict(name='BSF',
                            units='kg/m^2/s',)}
                    
plot_event_met(sos_5min_h2o_flux_ds, dates, vars, var_type_dict)

### February 4-7, 2023 -

In [89]:
dates = ('2023-01-29', '2023-02-07')
vars = ['P_10m_c', 'T_3m_c', 'spd_10m_c', 'dir_10m_c', 'sublimation_hourly_rate', 'precip_rate', 'SF_avg_1m_ue']
var_type_dict = {'sublimation_hourly_rate':
                    dict(name='sublimation',
                        units='mm/hr',),
                        'P_10m_c':
                        dict(name='atm_pres',
                            units='hPa',),
                        'T_3m_c':
                        dict(name='T_3m_c',
                            units='C',),
                        'spd_10m_c':
                        dict(name='spd_10m_c',
                            units='m/s',),
                        'dir_10m_c':
                        dict(name='dir_10m_c',
                            units='degrees',),
                        'precip_rate':
                        dict(name='precip_rate',
                            units='mm/hr',),
                        'SF_avg_1m_ue':
                        dict(name='BSF',
                            units='kg/m^2/s',)}
                    
plot_event_met(sos_5min_h2o_flux_ds, dates, vars, var_type_dict)

### March 5-7, 2023 - Broad Troughing over the PNW ushers zonal to SW flow over CO
A semi-stationary low pressure system off the OR/WA coast and short waves in the vicinity with a speedy jet streak aloft brought large sublimation totals to the East River with less precipitation.

In [85]:
dates = ('2023-03-03', '2023-03-07')
vars = ['P_10m_c', 'T_3m_c', 'spd_10m_c', 'dir_10m_c', 'sublimation_hourly_rate', 'precip_rate', 'SF_avg_1m_ue']
var_type_dict = {'sublimation_hourly_rate':
                    dict(name='sublimation',
                        units='mm/hr',),
                        'P_10m_c':
                        dict(name='atm_pres',
                            units='hPa',),
                        'T_3m_c':
                        dict(name='T_3m_c',
                            units='C',),
                        'spd_10m_c':
                        dict(name='spd_10m_c',
                            units='m/s',),
                        'dir_10m_c':
                        dict(name='dir_10m_c',
                            units='degrees',),
                        'precip_rate':
                        dict(name='precip_rate',
                            units='mm/hr',),
                        'SF_avg_1m_ue':
                        dict(name='BSF',
                            units='kg/m^2/s',)}
                    
plot_event_met(sos_5min_h2o_flux_ds, dates, vars, var_type_dict)

### March 22, 2023 - Rocky Mountain Cold Front I
An incoming low pressure system to California brought a cold front with it that traversed the range. This

In [82]:
dates = ('2023-03-21', '2023-03-24')
vars = ['P_10m_c', 'T_3m_c', 'spd_10m_c', 'dir_10m_c', 'sublimation_hourly_rate', 'precip_rate', 'SF_avg_2m_ue']
var_type_dict = {'sublimation_hourly_rate':
                    dict(name='sublimation',
                        units='mm/hr',),
                        'P_10m_c':
                        dict(name='atm_pres',
                            units='hPa',),
                        'T_3m_c':
                        dict(name='T_3m_c',
                            units='C',),
                        'spd_10m_c':
                        dict(name='spd_10m_c',
                            units='m/s',),
                        'dir_10m_c':
                        dict(name='dir_10m_c',
                            units='degrees',),
                        'precip_rate':
                        dict(name='precip_rate',
                            units='mm/hr',),
                        'SF_avg_2m_ue':
                        dict(name='BSF',
                            units='kg/m^2/s',)}
                    
plot_event_met(sos_5min_h2o_flux_ds, dates, vars, var_type_dict)

### March 30, 2023 - Rocky Mountain Cold Front II
An incoming low pressure system to California brought a cold front with it that traversed the range. This

In [84]:
dates = ('2023-03-27', '2023-04-01')
vars = ['P_10m_c', 'T_3m_c', 'spd_10m_c', 'dir_10m_c', 'sublimation_hourly_rate', 'precip_rate', 'SF_avg_2m_ue']
var_type_dict = {'sublimation_hourly_rate':
                    dict(name='sublimation',
                        units='mm/hr',),
                        'P_10m_c':
                        dict(name='atm_pres',
                            units='hPa',),
                        'T_3m_c':
                        dict(name='T_3m_c',
                            units='C',),
                        'spd_10m_c':
                        dict(name='spd_10m_c',
                            units='m/s',),
                        'dir_10m_c':
                        dict(name='dir_10m_c',
                            units='degrees',),
                        'precip_rate':
                        dict(name='precip_rate',
                            units='mm/hr',),
                        'SF_avg_2m_ue':
                        dict(name='BSF',
                            units='kg/m^2/s',)}
                    
plot_event_met(sos_5min_h2o_flux_ds, dates, vars, var_type_dict)